In [5]:
from google.colab import files
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import re
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.ensemble import RandomForestClassifier
from imblearn.over_sampling import SMOTE
from sklearn.metrics import f1_score, accuracy_score, precision_score

In [7]:
files.upload()


Saving labeled2.csv to labeled2.csv
Saving labeled3.csv to labeled3.csv
Saving old_queue32.csv to old_queue32.csv
Saving labeled4.csv to labeled4.csv
Saving labeled.csv to labeled.csv


{'labeled.csv': b'username,to,text,retweets,favorites,replies,tweet_id,permalink,author_id,date,formatted_date,hashtags,mentions,geo,urls,user_location,month,processed_text,label,annotations,annotation_approver,lab_final\nVipinHeartsTay,,"The fact their might be so many marital rape and other sexual assaults within homes taking place right now with a greater rate, and no one wont be talking about it bcz CORONA.",0,10,1,1255927001006903297,https://twitter.com/VipinHeartsTay/status/1255927001006903297,2875165356,2020-04-30 18:28:25+00:00,Thu Apr 30 18:28:25 +0000 2020,,,,,India,4,"fact might many marital rape sexual assault within home taking place right greater rate, one wont talking bcz corona.",DV,"[{\'label\': 24, \'user\': 1}]",admin,DV_OPINION_ADVOCATE\nTheGhoudi,,"\xe2\x80\x98If the child has been through sexual abuse, adults/Parents should give the child some space &amp; not be pushy + don\xe2\x80\x99t make them feel like it\xe2\x80\x99s the end of the world - please tell them it

In [8]:
data1 = pd.read_csv("labeled.csv")
data2 = pd.read_csv("labeled2.csv")
data3 = pd.read_csv("labeled3.csv")
data4 = pd.read_csv("labeled4.csv")
data5 = pd.read_csv("old_queue32.csv")

In [11]:
data1 = data1[["text","lab_final"]]
data2 = data2[["text","lab_final"]]
data3 = data3[["text","lab_final"]]
data4 = data4[["text","lab_final"]]
data5 = data5[["text","lab_final"]]

In [12]:
data = pd.concat([data1,data2,data3,data4,data5])

In [13]:
data.shape

(8957, 2)

In [14]:
data.duplicated().sum()

4336

In [15]:
data = data.drop_duplicates()

In [16]:
data.lab_final.value_counts()

NON_D_VIOLENCE_ABOUT       2613
NO_VIOLENCE                1057
NON_D_VIOLENCE_DIRECTED     437
DV_OPINION_INFO_NEWS        207
DV_OPINION_ADVOCATE         180
DV_STORY                     77
DV_OPINION_NEWS_INFO         20
DV_OPINION_DENIER            20
UNKNOWN                      10
Name: lab_final, dtype: int64

In [28]:
def stemming(words):
    ps = nltk.stem.SnowballStemmer('english')
    new = []
    stem_words = [ps.stem(x) for x in words]
    return stem_words

In [41]:
def preprocess(sentence):
    #sentence = contractions.fix(sentence)             # Replace contractions in string 
    sentence = re.sub('@\w+',"",str(sentence))        # remove mentions
    sentence = re.sub('#\w+',"",str(sentence))        # remove hashtags
    sentence = re.sub('http\S+',"",str(sentence))     # remove URLs
    sentence = re.sub('[^\w\s]'," ",str(sentence))    # remove punc
    sentence = re.sub('[^a-zA-Z]'," ",str(sentence))  # remove numbers

    sents = word_tokenize(sentence)                   # Tokenization
    sents = stemming(sents)
    
    stopword = stopwords.words('english')
    new_sents = ""
    for i in range(len(sents)):                       # remove stopwords            
        if(sents[i].lower() not in stopword and sents[i]!='rt'):
            new_sents += sents[i].lower()+" "
    new_sents.strip()
    
    return new_sents

In [42]:
def preprocessing(x_train,x_test,y_train,y_test):
  corpus_train = x_train.apply(preprocess)
  corpus_test = x_test.apply(preprocess)
  return corpus_train, y_train, corpus_test, y_test

In [43]:
target = data.lab_final
x = data["text"]

In [44]:
target.replace("DV_OPINION_INFO_NEWS",value="DV_OPINION",inplace=True)
target.replace("DV_OPINION_ADVOCATE",value="DV_OPINION",inplace=True)
target.replace("NON_D_VIOLENCE_DIRECTED",value="NON_D_VIOLENCE_ABOUT",inplace=True)

In [45]:
x_train,x_test,y_train,y_test = train_test_split(x,target, test_size=0.2, stratify=target)

In [46]:
x_train,y_train,x_test,y_test = preprocessing(x_train,x_test,y_train,y_test)

In [47]:
tf = TfidfVectorizer()
x_train_new = tf.fit_transform(x_train)
x_test_new = tf.transform(x_test)

In [48]:
sm = SMOTE()
x_train_smote, y_train_smote = sm.fit_resample(x_train_new,y_train)

/usr/local/lib/python3.6/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)


In [49]:
rf = RandomForestClassifier()
rf.fit(x_train_smote,y_train_smote)
predictions = rf.predict(x_test_new)

In [58]:
print("The Random Forest Model has accuracy {:.2f}".format(accuracy_score(y_test,predictions)))

The Random Forest Model has accuracy 0.88
